In [3]:
import json
import csv

# Load JSON objects as dictionary
df = json.load(open('drive/MyDrive/Colab_Notebooks/123/education.json'))
df_black = json.load(open('drive/MyDrive/Colab_Notebooks/123/education_black.json'))

# Order the datasets by area_name and year collected
df = sorted(df, key=lambda x: (x['area_name'], x['year'], x['variable']))
df_black = sorted(df_black, key=lambda x: (x['area_name'], x['year']))

# Clean the education dataset
df = [entry for entry in df if "25" in entry['variable'] and
      "Native" not in entry['variable'] and
      "Black" not in entry['variable'] and
      "White" not in entry['variable']]

# Rename the variable in both datasets for matching convenience
for entry in df:
    variable = entry['variable']
    if 'College Graduates' in variable:
        entry['variable'] = 'College Graduates'
    elif 'High School Graduates' in variable:
        entry['variable'] = 'High School Graduates'
    elif 'Elementary School Education or Less' in variable:
        entry['variable'] = 'Elementary School Education'
    elif 'Less Than 5 Years of Elementary School' in variable:
        entry['variable'] = 'Less Than 5 Years of Elementary School'

for entry in df_black:
    variable = entry['variable']
    if 'College' in variable:
        entry['variable'] = 'College Graduates'
    elif 'High School Graduate' in variable:
        entry['variable'] = 'High School Graduates'
    elif 'Less than High School' in variable:
        entry['variable'] = 'Elementary School Education'

# Re-structure the datasets
transformed_df = {}
for entry in df:
    area_name = entry['area_name']
    area_type = entry['area_type']
    year = entry['year']
    variable = entry['variable']
    value = entry['value']

    if area_name not in transformed_df:
        transformed_df[area_name] = {
            "area_type": area_type,
            "years": {}
        }

    if year not in transformed_df[area_name]["years"]:
        transformed_df[area_name]["years"][year] = []

    transformed_df[area_name]["years"][year].append({
        "variable": variable,
        "value": value
    })

transformed_df_black = {}
for entry in df_black:
    area_name = entry['area_name']
    area_type = entry['area_type']
    year = entry['year']
    variable = entry['variable']
    value = entry['value']

    if area_name not in transformed_df_black:
        transformed_df_black[area_name] = {
            "area_type": area_type,
            "years": {}
        }

    if year not in transformed_df_black[area_name]["years"]:
        transformed_df_black[area_name]["years"][year] = []

    transformed_df_black[area_name]["years"][year].append({
        "variable": variable,
        "value_black": value
    })

# Combine the datasets
result = {}
for area_name, area_data in transformed_df.items():
    if area_name in transformed_df_black:
        result[area_name] = {'area_type': area_data['area_type'], 'years': {}}
        for year, year_data in area_data['years'].items():
            if year in transformed_df_black[area_name]['years']:
                result[area_name]['years'][year] = year_data

for area_name, area_data in result.items():
    for year, year_data in area_data['years'].items():
        for entry in year_data:
            variable = entry['variable']
            black_year_data = transformed_df_black.get(area_name, {}).get('years', {}).get(year, [])
            black_entry = next((e for e in black_year_data if e['variable'] == variable), None)
            if black_entry:
                entry['value_black'] = black_entry['value_black']
            else:
                entry['value_black'] = None

# Save the nested structure data to JSON
file_path = '/content/drive/MyDrive/Colab_Notebooks/NC_Education/NC_Education_Nested.json'
with open(file_path, 'w') as json_file:
    json.dump(result, json_file)

In [ ]:
# Flatten the data and write to CSV
csv_data = []
for area_name, area_data in result.items():
    area_type = area_data['area_type']
    for year, year_data in area_data['years'].items():
        for entry in year_data:
            csv_data.append({
                'area_name': area_name,
                'area_type': area_type,
                'year': year,
                'variable': entry['variable'],
                'value': entry['value'],
                'value_black': entry['value_black']
            })

file_path = '/content/drive/MyDrive/Colab_Notebooks/Previous/NC_Education_Final.csv'
with open(file_path, 'w', newline='') as csv_file:
    fieldnames = ['area_name', 'area_type', 'year', 'variable', 'value', 'value_black']
    writer = csv.DictWriter(csv_file, fieldnames=fieldnames)

    writer.writeheader()
    writer.writerows(csv_data)